## Install dependencies

In [1]:
%pip install -r requirements.txt


[notice] A new release of pip is available: 24.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd
from pymongo import MongoClient
from pyspark.sql import SparkSession
import os
from pyspark.sql.functions import year

## Insert data into Mongodb

The datasets are currently files in .csv format, we have to import them into Mondodb

In [3]:
'''Insert ratings.csv into MongoDB'''
# load csv file into pandas DataFrame first
df = pd.read_csv("dataset/ml-latest/ratings.csv")

# =specify Mongodb client, database and collection
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

# convert DataFrame to a list of dictionaries (one for each row)
data = df.to_dict(orient="records")

# insert data into MongoDB
collection.insert_many(data)

InsertManyResult([ObjectId('6731eed04ea532ce5e7b09fd'), ObjectId('6731eed04ea532ce5e7b09fe'), ObjectId('6731eed04ea532ce5e7b09ff'), ObjectId('6731eed04ea532ce5e7b0a00'), ObjectId('6731eed04ea532ce5e7b0a01'), ObjectId('6731eed04ea532ce5e7b0a02'), ObjectId('6731eed04ea532ce5e7b0a03'), ObjectId('6731eed04ea532ce5e7b0a04'), ObjectId('6731eed04ea532ce5e7b0a05'), ObjectId('6731eed04ea532ce5e7b0a06'), ObjectId('6731eed04ea532ce5e7b0a07'), ObjectId('6731eed04ea532ce5e7b0a08'), ObjectId('6731eed04ea532ce5e7b0a09'), ObjectId('6731eed04ea532ce5e7b0a0a'), ObjectId('6731eed04ea532ce5e7b0a0b'), ObjectId('6731eed04ea532ce5e7b0a0c'), ObjectId('6731eed04ea532ce5e7b0a0d'), ObjectId('6731eed04ea532ce5e7b0a0e'), ObjectId('6731eed04ea532ce5e7b0a0f'), ObjectId('6731eed04ea532ce5e7b0a10'), ObjectId('6731eed04ea532ce5e7b0a11'), ObjectId('6731eed04ea532ce5e7b0a12'), ObjectId('6731eed04ea532ce5e7b0a13'), ObjectId('6731eed04ea532ce5e7b0a14'), ObjectId('6731eed04ea532ce5e7b0a15'), ObjectId('6731eed04ea532ce5e7b0a

In [4]:
'''Insert movies.csv into MongoDB'''
file_path = os.path.join('dataset', 'ml-latest', 'movies.csv')

df = pd.read_csv(file_path)

client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["movies"]

data = df.to_dict(orient="records")
collection.insert_many(data)

InsertManyResult([ObjectId('6731eed24ea532ce5e7c93e2'), ObjectId('6731eed24ea532ce5e7c93e3'), ObjectId('6731eed24ea532ce5e7c93e4'), ObjectId('6731eed24ea532ce5e7c93e5'), ObjectId('6731eed24ea532ce5e7c93e6'), ObjectId('6731eed24ea532ce5e7c93e7'), ObjectId('6731eed24ea532ce5e7c93e8'), ObjectId('6731eed24ea532ce5e7c93e9'), ObjectId('6731eed24ea532ce5e7c93ea'), ObjectId('6731eed24ea532ce5e7c93eb'), ObjectId('6731eed24ea532ce5e7c93ec'), ObjectId('6731eed24ea532ce5e7c93ed'), ObjectId('6731eed24ea532ce5e7c93ee'), ObjectId('6731eed24ea532ce5e7c93ef'), ObjectId('6731eed24ea532ce5e7c93f0'), ObjectId('6731eed24ea532ce5e7c93f1'), ObjectId('6731eed24ea532ce5e7c93f2'), ObjectId('6731eed24ea532ce5e7c93f3'), ObjectId('6731eed24ea532ce5e7c93f4'), ObjectId('6731eed24ea532ce5e7c93f5'), ObjectId('6731eed24ea532ce5e7c93f6'), ObjectId('6731eed24ea532ce5e7c93f7'), ObjectId('6731eed24ea532ce5e7c93f8'), ObjectId('6731eed24ea532ce5e7c93f9'), ObjectId('6731eed24ea532ce5e7c93fa'), ObjectId('6731eed24ea532ce5e7c93

## Use Apache Spark for parallel data processing

### Initial a Spark Session

In [5]:
spark = SparkSession.builder \
    .appName("Big-Data-Demo") \
    .master("local[*]") \
    .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
    .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/test")  \
    .getOrCreate() \

print(f"----------spark version: {spark.version}------------")

----------spark version: 3.5.3------------


### Load data from MongoDB

In [6]:
# load all data from MongoDB
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.ratings")\
    .load()    

df_movies = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.movies")\
    .load()   

# Show the loaded data
print(f"Original Rating Data:")
print(df_movies.show())
print(f"Original Movie Data:")
print( df_movies.show())

Original Rating Data:
+--------------------+--------------------+-------+--------------------+
|                 _id|              genres|movieId|               title|
+--------------------+--------------------+-------+--------------------+
|{6731d7505d382ee9...|Adventure|Animati...|      1|    Toy Story (1995)|
|{6731d7505d382ee9...|Adventure|Childre...|      2|      Jumanji (1995)|
|{6731d7505d382ee9...|      Comedy|Romance|      3|Grumpier Old Men ...|
|{6731d7505d382ee9...|Comedy|Drama|Romance|      4|Waiting to Exhale...|
|{6731d7505d382ee9...|              Comedy|      5|Father of the Bri...|
|{6731d7505d382ee9...|Action|Crime|Thri...|      6|         Heat (1995)|
|{6731d7505d382ee9...|      Comedy|Romance|      7|      Sabrina (1995)|
|{6731d7505d382ee9...|  Adventure|Children|      8| Tom and Huck (1995)|
|{6731d7505d382ee9...|              Action|      9| Sudden Death (1995)|
|{6731d7505d382ee9...|Action|Adventure|...|     10|    GoldenEye (1995)|
|{6731d7505d382ee9...|Comedy|

In [7]:
# load data according a query
query = '{"rating": {"$gt": 4}}'

df_ratings_filtered = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.ratings")\
    .option("spark.mongodb.input.query", query).load()  

print(f"Filtered Data (movies with rating > 4):")
print(df_ratings_filtered.show())

print(df_ratings_filtered.take(3)[0])

Filtered Data (movies with rating > 4):
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6731d74e5d382ee9...|      1|   4.0|964982703|     1|
|{6731d74e5d382ee9...|      3|   4.0|964981247|     1|
|{6731d74e5d382ee9...|      6|   4.0|964982224|     1|
|{6731d74e5d382ee9...|     47|   5.0|964983815|     1|
|{6731d74e5d382ee9...|     50|   5.0|964982931|     1|
|{6731d74e5d382ee9...|     70|   3.0|964982400|     1|
|{6731d74e5d382ee9...|    101|   5.0|964980868|     1|
|{6731d74e5d382ee9...|    110|   4.0|964982176|     1|
|{6731d74e5d382ee9...|    151|   5.0|964984041|     1|
|{6731d74e5d382ee9...|    157|   5.0|964984100|     1|
|{6731d74e5d382ee9...|    163|   5.0|964983650|     1|
|{6731d74e5d382ee9...|    216|   5.0|964981208|     1|
|{6731d74e5d382ee9...|    223|   3.0|964980985|     1|
|{6731d74e5d382ee9...|    231|   5.0|964981179|     1|
|{6731d74e5d382ee9...|   

### Spark's dataframe operations

In [ ]:
joined_df = df_movies.join(df_ratings, on="movieId", how="right")
print(f"movies_ratings_df:")
print(joined_df.columns)
# print(joined_df.select("timestamp").show())

movies_ratings_df:
['movieId', '_id', 'genres', 'title', '_id', 'rating', 'timestamp', 'userId']
+---------+
|timestamp|
+---------+
|964982703|
|964982703|
|964982703|
|964982703|
|964982703|
|964982703|
|964982703|
|964982703|
|964981247|
|964981247|
|964981247|
|964981247|
|964981247|
|964981247|
|964981247|
|964981247|
|964982224|
|964982224|
|964982224|
|964982224|
+---------+
only showing top 20 rows

None


### Create a new column named "Year"

In [ ]:
from pyspark.sql.functions import substring
from pyspark.sql.functions import col

joined_df = joined_df.withColumn("year", substring("title", -5, 4))
joined_df = joined_df.filter(col("year").rlike("^[12]"))
joined_df = joined_df.withColumn("year", col("year").cast("int"))

joined_df.show()
# joined_df.select("year").distinct().show()

+-------+--------------------+--------------------+--------------------+--------------------+------+---------+------+----+
|movieId|                 _id|              genres|               title|                 _id|rating|timestamp|userId|year|
+-------+--------------------+--------------------+--------------------+--------------------+------+---------+------+----+
|   1580|{6731eed24ea532ce...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6731d74e5d382ee9...|   3.0|964981125|     1|1997|
|   1580|{6731ed98fdc3910c...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6731d74e5d382ee9...|   3.0|964981125|     1|1997|
|   1580|{6731ed1d9b262373...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6731d74e5d382ee9...|   3.0|964981125|     1|1997|
|   1580|{6731e88756cb2d40...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6731d74e5d382ee9...|   3.0|964981125|     1|1997|
|   1580|{6731e730356e73e5...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6731d74e5d382ee9...|   3.0|964981125|     1|1997|
|   1580|{6731e6

## Train a movie recommender model

In [11]:
# recommender = RecommendationEngine(joined_df)

In [12]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression
from pyspark.ml.evaluation import RegressionEvaluator

In [24]:
feature_assembler = VectorAssembler(inputCols=["userId", "movieId"], outputCol="features")
assembled_df = feature_assembler.transform(joined_df)
(training_data, test_data) = assembled_df.randomSplit([0.8, 0.2])

model = LinearRegression(featuresCol="features", labelCol="rating", predictionCol="prediction")
lr_model = model.fit(training_data)

In [26]:
# make predictions
predictions = lr_model.transform(test_data)

# show predictions
predictions.select("features", "rating", "prediction").show()

# evaluate the model using R2 and RMSE
evaluator = RegressionEvaluator(labelCol="rating", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print(f"Root Mean Squared Error (RMSE): {rmse}")

evaluator.setMetricName("r2")
r2 = evaluator.evaluate(predictions)
print(f"R2: {r2}")

+------------+------+------------------+
|    features|rating|        prediction|
+------------+------+------------------+
|  [6.0,31.0]|   3.0|3.5935924550276908|
|[162.0,31.0]|   4.0|3.5498632915061674|
|[337.0,31.0]|   5.0|3.5008081401198425|
|[483.0,31.0]|   2.0|3.4598821281061087|
|[109.0,31.0]|   3.0|3.5647199944974544|
|[181.0,31.0]|   3.0|3.5445373036413663|
|[426.0,31.0]|   5.0| 3.475860091700512|
|[447.0,31.0]|   4.0|3.4699734735341528|
|[131.0,31.0]|   3.0|3.5585530611803162|
|[159.0,31.0]|   3.5|3.5507042369585045|
|[162.0,31.0]|   4.0|3.5498632915061674|
|[181.0,31.0]|   3.0|3.5445373036413663|
|[203.0,31.0]|   3.5| 3.538370370324228|
|[307.0,31.0]|   1.5|3.5092175946432125|
|[314.0,31.0]|   3.0|3.5072553885877595|
|[437.0,31.0]|   4.0|3.4727766250419427|
|[447.0,31.0]|   4.0|3.4699734735341528|
|[464.0,31.0]|   4.0|  3.46520811597091|
|[561.0,31.0]|   2.5| 3.438017546345347|
|  [6.0,31.0]|   3.0|3.5935924550276908|
+------------+------+------------------+
only showing top

In [ ]:
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.recommendation import ALS
from pyspark.sql import Row

ratings = joined_df.select("userId", "movieId", "rating")
(training, test) = ratings.randomSplit([0.8, 0.2])

# set cold start strategy to 'drop' to ensure we don't get NaN evaluation metrics
als = ALS(maxIter=5, regParam=0.01, userCol="userId", itemCol="movieId", ratingCol="rating",
          coldStartStrategy="drop")
model = als.fit(training)

# evaluate
predictions = model.transform(test)
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating",
                                predictionCol="prediction")
rmse = evaluator.evaluate(predictions)
print("Root-mean-square error = " + str(rmse))

# top 10 movie recommendations for each user
userRecs = model.recommendForAllUsers(10)
# top 10 user recommendations for each movie
movieRecs = model.recommendForAllItems(10)

# top 10 movie recommendations for a specified set of users
users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)

# top 10 user recommendations for a specified set of movies
movies = ratings.select(als.getItemCol()).distinct().limit(3)
movieSubSetRecs = model.recommendForItemSubset(movies, 10)

Root-mean-square error = 0.538042612130651


In [ ]:
print(userRecs.show())

+------+--------------------+
|userId|     recommendations|
+------+--------------------+
|     1|[{945, 6.9002323}...|
|     2|[{6380, 7.6768894...|
|     3|[{92420, 6.368151...|
|     4|[{5666, 6.3266077...|
|     5|[{1243, 7.579549}...|
|     6|[{27611, 6.512519...|
|     7|[{130518, 8.39599...|
|     8|[{2693, 8.861821}...|
|     9|[{58301, 8.285681...|
|    10|[{26258, 7.073716...|
|    11|[{3476, 9.082434}...|
|    12|[{3925, 9.284978}...|
|    13|[{86377, 8.669381...|
|    14|[{1354, 9.348432}...|
|    15|[{1658, 8.423873}...|
|    16|[{2360, 4.6792865...|
|    17|[{3925, 6.625032}...|
|    18|[{3925, 5.659679}...|
|    19|[{130518, 4.88170...|
|    20|[{6370, 7.0244074...|
+------+--------------------+
only showing top 20 rows

None
